In [1]:
%load_ext autoreload
%autoreload 2

%matplotlib qt

# mesmerize $\rightarrow$ Jupyter
Reading data from mesmerize batches to Jupyter to work directly in Python. Examples of three tasks:

1) [Get the batch dataframe](#batch) using the pandas dataframe that is automatically created by mesmerize.   
2) [Motion correction analysis](#motin): extract/examine files created for motion correction.    
3) [CNMF-E analysis](#cnmfe): extract/examine files created by the cnmfe-e algorithm.    

Note that the second and third steps use the dataframe created in the first step.

In [2]:
import matplotlib.pyplot as plt
import numpy as np
import os.path
import pandas as pd
import joblib

import caiman as cm
from caiman.source_extraction.cnmf.cnmf import load_CNMF

from bokeh.io import output_notebook
output_notebook()

Loading BokehJS ...

<a id="batch"></a>
# 1. Extract batch dataframe
Each batch directory has a pickle file called `dataframe.batch` that contains all the metadata you will need about each batch that was run: the module (e.g., `CNMFE`), input parameters, the unique identifier for that batch (`uuid`), the `name` used for that batch. You can read this data using `pd.read_pickle()`:

In [ ]:
batch_dir = #insert path to your batch directory here

In [4]:
batch_path = batch_dir + "dataframe.batch"
batch_df = pd.read_pickle(batch_path) 
batch_df.head() 

module  \
0  caiman_motion_correction   
1  caiman_motion_correction   
2                     CNMFE   
3                     CNMFE   
4  caiman_motion_correction   

                                        input_params output  \
0  {'output_bit_depth': 'Do not convert', 'templa...   None   
1  {'output_bit_depth': 'Do not convert', 'templa...   None   
2  {'item_name': 'snr2_rval6', 'do_cnmfe': True, ...   None   
3  {'item_name': 'snr3_r7', 'do_cnmfe': True, 'do...   None   
4  {'output_bit_depth': 'Do not convert', 'templa...   None   

                                                info  \
0  {'output_bit_depth': 'Do not convert', 'templa...   
1  {'output_bit_depth': 'Do not convert', 'templa...   
2  {'item_name': 'snr2_rval6', 'do_cnmfe': True, ...   
3  {'item_name': 'snr3_r7', 'do_cnmfe': True, 'do...   
4  {'output_bit_depth': 'Do not convert', 'templa...   

                                   uuid save_temp_files input_item  \
0  3da85508-ec6a-4615-803d-f2bbcd59a0fe               0       None   
1  4317fbed-243b-4111-b5c9-72cfc22d5bae               0       None   
2  fff45968-87d8-4622-b128-2e610a6f6754               0       None   
3  bbca365c-c051-4cac-bda0-753e6eabd4f3               0       None   
4  4767a5e5-3095-41e2-86ab-62092b1c29d6               0       None   

                     name  
0                motion90  
1               motion150  
2              snr2_rval6  
3                 snr3_r7  
4  lab_meeting_parameters

To see what modules you used:

In [5]:
batch_df.module.unique()

array(['caiman_motion_correction', 'CNMFE'], dtype=object)

<a id="motion"></a>
# 2. Motion correction results
This assumes you have run a batch using the `caiman_motion_correction` module. We'll extract the `uuid` as a string. This unique id is important as it is a unique identifier for each batch, and is used by Mesmerize to name every file for that batch. 

In [6]:
mc_ind = 0  # index to pull among motion-corrected batches
mc_batch = batch_df[batch_df.module == 'caiman_motion_correction'].iloc[mc_ind]
mc_uuid = mc_batch.uuid
mc_uuid_string = str(mc_uuid)
print(mc_batch)

module                                      caiman_motion_correction
input_params       {'output_bit_depth': 'Do not convert', 'templa...
output                                                          None
info               {'output_bit_depth': 'Do not convert', 'templa...
uuid                            3da85508-ec6a-4615-803d-f2bbcd59a0fe
save_temp_files                                                    0
input_item                                                      None
name                                                        motion90
Name: 0, dtype: object


There are many files associated with this batch that you can explore using the `uuid` (you can get them using `glob.glob(batch_dir + mc_uuid_string + '*')`, but we are most interested in the motion-corrected movie, which will be named `<uuid>_mc.tiff`.

In [8]:
mc_movie_filename = mc_uuid_string + '_mc.tiff'
mc_movie_path = batch_dir + mc_movie_filename
# make sure it is present
if os.path.isfile(mc_movie_path):
    print(f"{mc_movie_filename} exists")
else:
    print("No mc movie file")

3da85508-ec6a-4615-803d-f2bbcd59a0fe_mc.tiff exists


You can check which parameters you ran for motion correction in this batch.

In [9]:
mc_params = mc_batch['input_params'].item()['mc_kwargs']
mc_params

{'max_shifts': (10, 10),
 'niter_rig': 3,
 'max_deviation_rigid': 6,
 'strides': (90, 90),
 'overlaps': (45, 45),
 'upsample_factor_grid': 4,
 'gSig_filt': (5, 5)}

## Load/display motion corrected movie
Here we start to get to the main point: connecting mesmerize results to `caimain` methods/functions. Here we use the caiman movie load/play functionality. Note if your movie is big this can be quite slow.

In [10]:
%%time
mc_movie = cm.load_movie_chain([mc_movie_path])
image_dims = mc_movie.shape[1:] #will be used below for mc metrics

100%|████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:23<00:00, 23.12s/it]


Wall time: 24.4 s


You can do many standard things with caiman movies that you can do with numpy arrays.

In [11]:
max_proj = np.max(mc_movie, axis = 0)
plt.imshow(max_proj, cmap = 'gray')

You can optionally display the motion corrected movie using its `display` method. Press **q** to quit the display. 

In [104]:
display_movie = True  #False for movies that are too large
if display_movie:
    ds_ratio = 0.2
    mc_movie.resize(1, 1, ds_ratio).play(gain = 0.8, 
                                         q_max=99.9, 
                                         q_min = 1, 
                                         fr=20, 
                                         magnification=1.5, 
                                         plot_text = True,
                                         do_loop = True)

## Extract motion correction evaluation metrics
One useful feature in caiman is the ability to extract quantitative metrics to evaluate the quality of motion correction (as discussed in detail in the NoRMCorre paper: https://pubmed.ncbi.nlm.nih.gov/28782629/). See the paper for details, but the three main evaluation metrics are the correlation with a template image (`correlations_metric`), the crispness measure (`crispness_metric`), and the residual optic flow  (`flows_metric`).

**CAVEAT**: this function can take a very long time to run. You can decrease `resize_fact_flow` to skip more frames in the optic flow calculation to speed it up. Also, note the following function will add the file `uuid_mc._metrics.npz` to your batch folder (`npz` is numpy's compressed array format).

In [112]:
%%time
gsig = mc_params['gSig_filt']
# metrics setup
final_size = image_dims #note not accounting for border effects here
winsize = 100
swap_dim = False
play_it = False  # this throws an error 
resize_fact_flow = .2    # downsample for computing optic flow

# metrics for original
template_metric, correlations_metric, flows_metric, norms_metric, crispness_metric = \
      cm.motion_correction.compute_metrics_motion_correction(mc_movie_path, 
                                                             final_size[0], 
                                                             final_size[1], 
                                                             swap_dim, 
                                                             winsize=winsize, 
                                                             play_flow= play_it, 
                                                             resize_fact_flow=resize_fact_flow,
                                                             gSig_filt = gsig);

Wall time: 3min 59s


First, check out correlation with template 

In [120]:
print(f"corr: {np.mean(correlations_metric)}")

plt.figure('Correlation metric')
plt.plot(correlations_metric); 
plt.autoscale(enable=True, axis='x', tight=True);
plt.title('Correlation with template');
plt.xlabel('Frame#')
plt.ylabel('Correlation');

corr: 0.7920198383012961


Second, check out norm of residual optic flow fields

In [121]:
print(f"Motion residual: {np.mean(norms_metric)}")

# Plot overall
plt.figure('Optic flow')
plt.plot(norms_metric); 
plt.xlabel('frame (factored)')
plt.ylabel('motion energy')
plt.title('Residual Optic Flow')
plt.autoscale(enable=True, axis='x', tight=True);

Motion residual: 10.381607055664062


Third, print crispness value

In [122]:
print(f"Crispness {crispness_metric}")

Crispness 363.8479309082031


As mentioned above, `motion_correction.compute_metrics_motion_correction()` automatically saves some results in  `<uuid>_mc._metrics.npz` that you can use for comparison with other mc parameters later. As a final step, let's just verify this worked.

In [12]:
mc_metrics_filename = mc_uuid_string + '_mc._metrics.npz'
if os.path.isfile(batch_dir + mc_metrics_filename):
    print(f"{mc_metrics_filename} exists")
else:
    print("No mc metrics file: something went wrong!")

3da85508-ec6a-4615-803d-f2bbcd59a0fe_mc._metrics.npz exists


<a id="cnmfe"></a>
# 3. CNMFE results
Most people's main use case will probably be for analyzing CNMF/CNMF-E results. The logic will be very similar to looking at motion corrected results. For each cnmfe the main files you will likely be interested in include:

- `uuid_results.hdf5`: the results of the analysis that let you reconstruct the estimates object
- `uuid_input.tiff`: input movie (motion corrected movie)
- `uuid_cn_filter.pikl`: correlation image (often useful in plotting)

Here we'll just walk through loading the movie, results, and correlation image

In [13]:
cnm_ind = 0  # index among motion-corrected batches
cnm_batch = batch_df[batch_df.module == 'CNMFE'].iloc[cnm_ind]
cnm_uuid = cnm_batch.uuid
cnm_uuid_string = str(cnm_uuid)
print(cnm_batch)

module                                                         CNMFE
input_params       {'item_name': 'snr2_rval6', 'do_cnmfe': True, ...
output                                                          None
info               {'item_name': 'snr2_rval6', 'do_cnmfe': True, ...
uuid                            fff45968-87d8-4622-b128-2e610a6f6754
save_temp_files                                                    0
input_item                                                      None
name                                                      snr2_rval6
Name: 2, dtype: object


Quickly check that the files exist.

In [14]:
cnm_results_filepath = batch_dir + cnm_uuid_string + '_results.hdf5'
cn_filepath = batch_dir + cnm_uuid_string + '_cn_filter.pikl'
cnm_movie_filepath = batch_dir + cnm_uuid_string + '_input.tiff'

# cnmfe results
if os.path.isfile(cnm_results_filepath):
    print(f"{cnm_results_filepath} exists")
else:
    print("No cnm file")

# correlation image array
if os.path.isfile(cn_filepath):
    print(f"{cn_filepath} exists")
else:
    print("No cn file")
    
# motion corrected movie array
if os.path.isfile(cnm_movie_filepath):
    print(f"{cnm_movie_filepath} exists")
else:
    print("No movie file")

F:/mesmerize_projects/anesthesia_clipped/batches/anesthesia_batches/fff45968-87d8-4622-b128-2e610a6f6754_results.hdf5 exists
F:/mesmerize_projects/anesthesia_clipped/batches/anesthesia_batches/fff45968-87d8-4622-b128-2e610a6f6754_cn_filter.pikl exists
F:/mesmerize_projects/anesthesia_clipped/batches/anesthesia_batches/fff45968-87d8-4622-b128-2e610a6f6754_input.tiff exists


## Check out correlation image

In [15]:
with open(cn_filepath, 'rb') as f:
    corr_img = joblib.load(f)   
plt.imshow(corr_img, cmap='inferno');

## Movie load and view
For large movies you might not want to do this.

In [132]:
%%time
fnames = [cnm_movie_filepath]  #this used to be download_demo when you use their data
movie = cm.load_movie_chain(fnames)

100%|████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:07<00:00,  7.58s/it]


Wall time: 8.96 s


In [134]:
display_movie = True  #False for movies that are too large
if display_movie:
    ds_ratio = 0.2
    movie.resize(1, 1, ds_ratio).play(gain = 0.8, 
                                      q_max=99.9, 
                                      q_min = 1,  
                                      fr=20, 
                                      magnification=1.5, 
                                      plot_text = True,
                                      do_loop = False)

### Optional: Create memory-mapped movie
If you didn't save your memmapped data in mesmerize, this will be needed for:
- `evaluate_components()` (used frequently for iteratively removing false positives) 
- `cnm.fit()` in case you ever want to re-run cnmf-e again

In [136]:
%%time
mapped_movie_path = cm.save_memmap([cnm_movie_filepath], base_name='memmap_', order='C');
# load memory mappable file
Yr, dims, T = cm.load_memmap(mapped_movie_path)
images_mm = Yr.T.reshape((T,) + dims, order='F')

Wall time: 18.1 s


## Reconstruct CNMF object
The hdf5 object that Mesmerize saves in the batch folder is the exact one that caiman uses for reconstructing the cmn object.  

In [139]:
#start a cluster for parallel processing 
num_cpus = 10
# note if a cluster already exists it will be closed so a new session will be opened
if 'dview' in locals():  # locals contains list of current local variables
    cm.stop_server(dview=dview)
c, dview, n_processes = cm.cluster.setup_cluster(backend='local', 
                                                 n_processes=num_cpus, 
                                                 single_thread=False,
                                                 ignore_preexisting=True)
#Number of nodes in cluster (keep this as separate cell you like to check on it sometimes)
print(f"Cluster has {n_processes} processes in the pool {type(dview)}");

Cluster has 10 processes in the pool <class 'multiprocessing.pool.Pool'>


Build the CNMF object from the hdf5 file:

In [140]:
cnm = load_CNMF(cnm_results_filepath, n_processes, dview=dview)

Now you have the full `CNMF` object that you would get if you had run things in caiman. You can access the various traces/components [as discussed in the documentation](https://caiman.readthedocs.io/en/master/Getting_Started.html#result-interpretation). There is also a [list of useful methods](https://caiman.readthedocs.io/en/master/core_functions.html#estimates). For some of them you need a movie input (which we have generated above as `movie`) for some you would like an image (which you might want to use the correlation image `corr_image` that we loaded above). 

We'll end with just a couple of examples, which should be familiar to users of `caiman`.

In [142]:
cnm.estimates.dims = cnm.dims
cnm.estimates.nb_view_components(img =  corr_img,
                                 cmap = 'gray',
                                 idx = cnm.estimates.idx_components,
                                 denoised_color = 'red',
                                 thr = 0.99);

The following can use a custom `img` param as input, or it will default to mean of all spatial components, which we have done here:

In [156]:
cnm.estimates.plot_contours_nb(params = cnm.params,
                               idx=cnm.estimates.idx_components,
                               cmap = 'gray');

There is obviously a lot more you can do once you have your data loaded into Jupyter or your favorite IDE. The point here was just to show the basic mechanics of how to ingest from Mesmerize batches into Jupyter to help get started. Good luck!